## Importando bibliotecas e dados

In [296]:
import pandas as pd
import plotly.express as px
import datetime
import numpy as np

In [297]:
costs_us = pd.read_csv('Files\costs_us.csv',parse_dates=['dt'],dtype={'source_id': 'category'})
orders_log = pd.read_csv('Files\orders_log_us.csv',parse_dates = ['Buy Ts'])
visits_log_us = pd.read_csv('Files\\visits_log_us.csv',parse_dates = ['End Ts','Start Ts'],dtype={'Device': 'category','Source Id': 'category'})

## Checking for null and duplicated values

In [298]:
# Checking for null values
costs_us.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   source_id  2542 non-null   category      
 1   dt         2542 non-null   datetime64[ns]
 2   costs      2542 non-null   float64       
dtypes: category(1), datetime64[ns](1), float64(1)
memory usage: 42.7 KB


In [299]:
# Checking for null values
orders_log.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype         
---  ------   --------------  -----         
 0   Buy Ts   50415 non-null  datetime64[ns]
 1   Revenue  50415 non-null  float64       
 2   Uid      50415 non-null  uint64        
dtypes: datetime64[ns](1), float64(1), uint64(1)
memory usage: 1.2 MB


In [300]:
# Checking for null values
visits_log_us.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
 #   Column     Non-Null Count   Dtype         
---  ------     --------------   -----         
 0   Device     359400 non-null  category      
 1   End Ts     359400 non-null  datetime64[ns]
 2   Source Id  359400 non-null  category      
 3   Start Ts   359400 non-null  datetime64[ns]
 4   Uid        359400 non-null  uint64        
dtypes: category(2), datetime64[ns](2), uint64(1)
memory usage: 8.9 MB


In [301]:
# Checking for duplicated values
print('Duplicated values - cost_us: ', costs_us.duplicated().sum())
print('Duplicated values - orders_log: ', orders_log.duplicated().sum())
print('Duplicated values - visits_log_us: ', visits_log_us.duplicated().sum())

Duplicated values - cost_us:  0
Duplicated values - orders_log:  0
Duplicated values - visits_log_us:  0


## About the product

### Dataframe editing

In [302]:
# Creating a date column

visits_log_us['duration (s)'] = (visits_log_us['End Ts'] - visits_log_us['Start Ts']).dt.total_seconds().round(2)
visits_log_us['Day'] = visits_log_us['Start Ts'].dt.date

In [303]:
# Creating a new DataFrame with 'Day' columns and all the unique user logs for each day.
# Followed by a change in the type of 'Day' column to datetime

visit_users_by = visits_log_us.groupby(['Day']).agg({'Uid':'nunique'}).reset_index()
visit_users_by['Day'] = visit_users_by['Day'].astype('datetime64[D]')

In [304]:
# Creation of columns 'week'and 'month

visit_users_by['Week'] = visit_users_by['Day'].dt.isocalendar().week
visit_users_by['Month'] = visit_users_by['Day'].dt.month


In [305]:
# Total of unique users that logged at the website per day

visit_users_by_day = visit_users_by.groupby(['Day']).agg({'Uid':'sum'}).reset_index()
visit_users_by_day.columns = ['Start_day','Total_users']

In [306]:
# Total of unique users that logged at the website per week

visit_users_by_week = visit_users_by.groupby(['Week']).agg({'Uid':'sum'}).reset_index()
visit_users_by_week.columns = ['Start_week','Total_users']

In [307]:
# Total of unique users that logged at the website per month

visit_users_by_month = visit_users_by.groupby(['Month']).agg({'Uid':'sum'}).reset_index()
visit_users_by_month.columns = ['Start_month','Total_users']

In [308]:
# Adding the name of the month to the visit_users_by_month dataframe

month_dict = pd.DataFrame({
    'number':[1,2,3,4,5,6,7,8,9,10,11,12],
    'month': ['January', 'February', 'March', 'April', 'May', 'June','July', 'August', 'September', 'October', 'November', 'December']
    }
)

visit_users_by_month = visit_users_by_month.merge(month_dict,
                                                  left_on = 'Start_month',
                                                  right_on= 'number').drop('number', axis=1)
#visit_users_by_month.head()

In [309]:
# Checking data output

print('Sum of unique users by month: ',visit_users_by_month['Total_users'].sum())
print('Sum of unique users by week: ',visit_users_by_week['Total_users'].sum())
print('Sum of unique users by day: ',visit_users_by_day['Total_users'].sum())
print('Total users: ',visits_log_us['Uid'].nunique())

Sum of unique users by month:  330509
Sum of unique users by week:  330509
Sum of unique users by day:  330509
Total users:  228169


### Graphic analysis - Count of unique users per day, week and month

In [310]:
# Mean value of total users column at the visit_users_by_month dataframe to add at the graph
mean_value = visit_users_by_month['Total_users'].mean()

# Bar graph creation - month data
visit_users_by_month_fig = px.bar(visit_users_by_month,
                                  x = 'month',
                                  y= 'Total_users')

visit_users_by_month_fig.update_layout(title = 'Total unique users per month',
                                       xaxis_title = 'Month',
                                       yaxis_title = 'Total unique users')

visit_users_by_month_fig.add_hline(y=mean_value,
                                   line_dash='dash',
                                   line_color='black')

visit_users_by_month_fig.update_traces(texttemplate= '%{y}',
                                       textposition='outside')

The information above shows us the total of unique users that logged at the platform. We can see a high decrease during the months of June, July and August. It is intereting to look further on reasons why this could be happening, I would be nice to compare this data with the costs dataset, where we can see all our expenses with marketing.

In [311]:
# Histogram graph creation - per day data
visit_users_by_day_fig = px.histogram(visit_users_by_day,
                                      x = 'Total_users')

visit_users_by_day_fig.update_layout(title = 'Total frequency of unique users per day',
                                     xaxis_title = 'Total users range',
                                     yaxis_title = 'Frequency')

visit_users_by_day_fig.update_traces(texttemplate= '%{y}',
                                     textposition='outside')

In [312]:
# Boxplot creation - per day data
visit_users_by_day_box = px.box(visit_users_by_day,
                                x = 'Total_users')

visit_users_by_day_box.update_layout(title = 'Unique users per day - Boxplot',
                                     xaxis_title = 'Total users')

visit_users_by_day_box.update_traces(boxmean=True)

In the graphs above we can identify the following:

- The lowest amount of user at the platform was 1;
- Our median is at 921 users;
- Having more than 1200 users a day is uncommon;
- Our highest amount of users at the platform was 3319 (which it make us wonder what happened that day);
- Our mean and median values are very similar (907.99 and 921)

In [313]:
# Mean value of total users column at the visit_users_by_week dataframe to add at the graph
mean_value = visit_users_by_week['Total_users'].mean()

# Bar graph creation - week data
visit_users_by_week_fig = px.bar(visit_users_by_week,
                                 x = 'Start_week',
                                 y = 'Total_users')

visit_users_by_week_fig.update_layout(title = 'Total unique user by week',
                                      xaxis_title = 'Week',
                                      yaxis_title = 'Total')

visit_users_by_week_fig.add_hline(y=mean_value,
                                  line_dash='dash',
                                  line_color='black')

Based on the graph above we can infer the following conclusions:
- From the week 23-38, it was the longest period of time where the platform reached numbers below the average;
- Weeks between 23-38 are related to the period between June and September, confirming the information idetified before, but we can still identify reasons for the decrease in user logs comparing to the dataset of marketing costs.

### Analysis of all log sessions per day, followed by a quick comparison with the unique log sessions per day

In [314]:
visits_log_us.head()

Device              End Ts Source Id            Start Ts  \
0    touch 2017-12-20 17:38:00         4 2017-12-20 17:20:00   
1  desktop 2018-02-19 17:21:00         2 2018-02-19 16:53:00   
2    touch 2017-07-01 01:54:00         5 2017-07-01 01:54:00   
3  desktop 2018-05-20 11:23:00         9 2018-05-20 10:59:00   
4  desktop 2017-12-27 14:06:00         3 2017-12-27 14:06:00   

                    Uid  duration (s)         Day  
0  16879256277535980062        1080.0  2017-12-20  
1    104060357244891740        1680.0  2018-02-19  
2   7459035603376831527           0.0  2017-07-01  
3  16174680259334210214        1440.0  2018-05-20  
4   9969694820036681168           0.0  2017-12-27

In [315]:
# Total visits per day dataframe - counting 
total_visits_day = visits_log_us.groupby('Day')['Uid'].count().reset_index(name = 'Count')
total_visits_day.head()

Day  Count
0  2017-06-01    664
1  2017-06-02    658
2  2017-06-03    477
3  2017-06-04    510
4  2017-06-05    893

In [316]:
# Total visits per day count vs Total unique visits perday count - boxplot

total_visits_day_fig = px.box(total_visits_day,
                              x = 'Count')

total_visits_day_fig.update_layout(title = 'Total users per day - Boxplot',
                                   xaxis_title = 'Total users')

total_visits_day_fig.update_traces(boxmean=True)

total_visits_day_fig.show()
visit_users_by_day_box

In [317]:
# Comparison between total users logs and total unique users logs

print('Total user logs: ',total_visits_day['Count'].sum())
print('\n')
print('Total unique user logs: ',visit_users_by_day['Total_users'].sum())

Total user logs:  359400


Total unique user logs:  330509


By comparing the two boxplots above, the first with all the user logs (including users that logged more than once a day) and the second with all the unique user logs, we identify that the median and the mean values are very similar.

### Logs sessions duration

In [318]:
visits_log_us.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 7 columns):
 #   Column        Non-Null Count   Dtype         
---  ------        --------------   -----         
 0   Device        359400 non-null  category      
 1   End Ts        359400 non-null  datetime64[ns]
 2   Source Id     359400 non-null  category      
 3   Start Ts      359400 non-null  datetime64[ns]
 4   Uid           359400 non-null  uint64        
 5   duration (s)  359400 non-null  float64       
 6   Day           359400 non-null  object        
dtypes: category(2), datetime64[ns](2), float64(1), object(1), uint64(1)
memory usage: 14.4+ MB


In [319]:
#Logs duration data separation and count of negative numbers, positive numbers and equal to zero.
logs_duration_equals_0_total = visits_log_us[visits_log_us['duration (s)']==0]['Uid'].count()
negative_logs_durations_total = visits_log_us[visits_log_us['duration (s)']<0]['Uid'].count()
positive_logs_durations_total = visits_log_us[visits_log_us['duration (s)']>0]['Uid'].count()

#Positive logs duration dataset
positive_logs_durations_df = visits_log_us[visits_log_us['duration (s)']>0]

In [320]:
# Counting of logs based on duration (equal to 0, positive and negative)

print (f"Quantidade de logs com duração de 0 segundos: {logs_duration_equals_0_total}")
print('\n')
print (f"Quantidade de logs com valores negativos: {negative_logs_durations_total}")
print('\n')
print (f"Quantidade de logs com valores positivos: {positive_logs_durations_total}")

Quantidade de logs com duração de 0 segundos: 35794


Quantidade de logs com valores negativos: 2


Quantidade de logs com valores positivos: 323604


In [321]:
# Grouped of positive logs and their user count
pos_logs_duration_analysis = positive_logs_durations_df.groupby(['duration (s)','Day']).agg({'Uid': 'count'}).reset_index()

#positive_logs_durations_df.sample()

In [322]:
#Mean value for positive logs duration
mean_log_value = pos_logs_duration_analysis['duration (s)'].mean()

#Histogram for analysis of positive logs duration
pos_logs_duration_analysis_fig = px.histogram(pos_logs_duration_analysis,
                                              x = 'duration (s)')

pos_logs_duration_analysis_fig.add_vline(x=mean_log_value,
                                         line_dash='dash',
                                         line_color='black')

pos_logs_duration_analysis_fig.update_layout(title = 'Frequency of duration in seconds for users',
                                             xaxis_title = 'Duration (s)',
                                             yaxis_title = 'Frequency')

In [323]:
#Boxplot for analysis of positive logs duration
pos_logs_duration_analysis_fig = px.box(pos_logs_duration_analysis,
                                        x = 'duration (s)')

#Added a line representing the mean value
pos_logs_duration_analysis_fig.add_vline(x=mean_log_value,
                                         line_dash='dash',
                                         line_color='black',
                                         line_width=0.8)

Above we can identify that most part of our duration values are below the average and that we have outliers that showes an high increase in the log duration.

In [324]:
# Code to identify how frequently users come back to the platform

#Creation of users frequency dataframe and median data for line creation on histogram
users_frequency = visits_log_us.groupby('Uid').agg(
    {'Day': 'nunique'}
    ).reset_index().sort_values(
        by = 'Uid',
        ascending = True)

# Median of the frequency value for users
median_us_freq = users_frequency['Day'].median()

#Users log frequency - Histogram
users_frequency_fig = px.histogram(
    users_frequency,
    x = 'Day',
    nbins = 250)

users_frequency_fig.add_vline(
    x = median_us_freq,
    line_dash = 'dash',
    line_color = 'black')

As we can see in the graph above, the majority of users do not return to the platform.

## About the sales

### Period from first visit to conversion

In [325]:
# Creation of date column
orders_log['Day'] = orders_log['Buy Ts'].dt.date
orders_log['Day'] = pd.to_datetime(orders_log['Day'])

In [326]:
# Creation of a DataFrame based on the day where they bought at the platform for the first time

orders_first_buy = orders_log.groupby(['Buy Ts','Uid']).agg({'Day':'min'}).reset_index()
orders_first_buy.columns = ['Buy Ts','Uid','Buy Day']
#orders_first_buy.sample()

In [327]:
# Creation of a DataFrame based on the day where they visited the platform for the first time

visits_first_visit = visits_log_us.groupby('Uid').agg({'Day':'min'}).reset_index()
visits_first_visit.columns = ['Uid','Visit Day']
visits_first_visit['Visit Day'] = pd.to_datetime(visits_first_visit['Visit Day'])
#visits_first_visit.sample()


In [328]:
# Dataframe with the conversion period between the first visit and the first buy

conversion_df = visits_first_visit.merge(orders_first_buy, on = 'Uid').drop(columns = ['Buy Ts'])
conversion_df['Time to Buy (days)'] = conversion_df['Buy Day'] - conversion_df['Visit Day']
conversion_df['Time to Buy (days)'] = conversion_df['Time to Buy (days)'].dt.days
#conversion_df.sample()

In [329]:
# Conversion histogram

conversion_time_fig = px.histogram(conversion_df,
                                   x='Time to Buy (days)',
                                   nbins=10)

conversion_time_fig.update_layout(
    title = 'Users frequency of period for conversion - first visit to first buy'
    )

In [330]:

# Total users
total_users_conversion = conversion_df['Time to Buy (days)'].count()

# Percentages calculations

zero_days_percent = (((conversion_df['Time to Buy (days)']==0).sum()/
                   total_users_conversion)*100).round(2)

one_to_6_days_percent = (((((conversion_df['Time to Buy (days)']>0) &
                           (conversion_df['Time to Buy (days)']<=6)).sum())/
                          total_users_conversion)*100).round(2)

seven_to_30_days_percent = (((((conversion_df['Time to Buy (days)']>7) &
                           (conversion_df['Time to Buy (days)']<=30)).sum())/
                          total_users_conversion)*100).round(2)

above_30_days_percent = (((((conversion_df['Time to Buy (days)'] > 30).sum()) /
                         total_users_conversion)*100)).round(2)

In [331]:
# Percentage of user logs frequency

print(f"Users that bought at the platform at their first visit: {zero_days_percent}%")
print('\n')
print(f"Users that bought at the platform from 1 to 6 days: {one_to_6_days_percent}%")
print('\n')
print(f"Users that bought at the platform from 1 to 6 days: {seven_to_30_days_percent}%")
print('\n')
print(f"Users that bought at the platform after 30 days: {above_30_days_percent}%")

Users that bought at the platform at their first visit: 52.35%


Users that bought at the platform from 1 to 6 days: 11.47%


Users that bought at the platform from 1 to 6 days: 8.61%


Users that bought at the platform after 30 days: 26.81%


### Sales per period

In [332]:
# All the sales during the first 29 days after the first sale
min_date = orders_log['Day'].min().date()
period_30_days = np.datetime64(min_date + datetime.timedelta(days=29))

# DataFrame for the first 30 days period
period_30_days_df = orders_log[orders_log['Day'] <= period_30_days]

# All the sales between the days 31 to 90 after the first sale
day_31 = np.datetime64(min_date + datetime.timedelta(days=30))
period_31_90_days = day_31 + 59

# DataFrame for the first 30 days period
period_31_90_days_df = orders_log[(orders_log['Day'] > period_30_days)&(orders_log['Day'] <= period_31_90_days)]

# All the sales between above 90 days after the first sale
day_90 = np.datetime64(min_date + datetime.timedelta(days=89))

# DataFrame above 60 days period
period_90_days_df = orders_log[orders_log['Day'] > day_90]

In [333]:
# Sales per period DataFrame

data = {'Period':['First 30 days',
                  '31 to 90 days',
                  'Above 90 days',
                  'Total sales'],
        'Total Sales':[period_30_days_df['Day'].count(),
                       period_31_90_days_df['Day'].count(),
                       period_90_days_df['Day'].count(),
                       orders_log['Day'].count()]}

period_sales_df = pd.DataFrame(data)

In [334]:
# Sales per period - Bar graph 

period_sales_df_fig = px.bar(
    period_sales_df,
    x ='Period',
    y='Total Sales',
    title = 'Count of sales per period - From the first sale')

period_sales_df_fig

In [335]:
print(f"First sale date: {orders_log['Day'].min().date()}")
print(f"First log date: {visits_log_us['Day'].min()}")

First sale date: 2017-06-01
First log date: 2017-06-01


In the graph above we can see that most of the sales happened after 90 days from the platform first sale and, since the platform first sale and first log were at the same day so if we consider the first log day as the website opening day, there were a 90 days period before the sales have high increase.

In [336]:
avg_revenue = float(orders_log['Revenue'].mean())
print(f"Average sale revenue: {avg_revenue:.2f}")

Average sale revenue: 5.00


## About the marketing

### Costs per source

In [337]:
# Costs per source - groupby

costs_by_source = costs_us.groupby('source_id').agg({'costs':'sum'}).reset_index()
costs_by_source.columns = ['Source Id','Costs']

In [338]:
categories = sorted(costs_by_source['Source Id'].cat.categories, key=lambda x: int(x))

# Costs per source - Bar graph

costs_by_source_fig = px.bar(
    costs_by_source,
    x = 'Source Id',
    y = 'Costs'
    )

costs_by_source_fig.update_layout(
    title = 'Costs per source',
    xaxis_title='Source',
    yaxis_title='Cost',
    xaxis={'tickvals': costs_by_source['Source Id'],
           'categoryorder': 'array',
           'categoryarray': categories}
)

In [339]:
print(f"Total costs: ${costs_us['costs'].sum()}")

Total costs: $329131.62


The third source had the higher marketing investment, and the total investment was $329131.61

### Costs per client log for each source

In [340]:
#Groupment of total log per each source

total_logs_per_source = visits_log_us.groupby('Source Id').agg({'Uid':'count'}).reset_index()
total_logs_per_source.columns = ['Source Id','Uid Count']

In [347]:
# Creation of DataFrame responsible for grouping the total amount of logs per source and their respective marketing cost

total_logs_per_source_cost = total_logs_per_source.merge(costs_by_source, on = 'Source Id', how = 'outer')
total_logs_per_source_cost['Avg log cost'] =  total_logs_per_source_cost['Costs'] / total_logs_per_source_cost['Uid Count']
total_logs_per_source_cost['Source Id'] = total_logs_per_source_cost['Source Id'].astype('int')
total_logs_per_source_cost = total_logs_per_source_cost.sort_values(by = 'Source Id', ascending=True)

In [348]:
#Average marketing cost per log

total_logs_per_source_cost_fig = px.bar(
    total_logs_per_source_cost,
    x = 'Source Id',
    y = 'Avg log cost')

total_logs_per_source_cost_fig.update_layout(
    xaxis = {'tickvals': total_logs_per_source_cost['Source Id']},
    title = 'Average marketing cost per log at each source'
    )

# Total logs per source
total_logs_per_source_fig = px.bar(total_logs_per_source_cost,
                                   x = 'Source Id',
                                   y = 'Uid Count')

total_logs_per_source_fig.update_layout(
    xaxis = {'tickvals': total_logs_per_source_cost['Source Id']},
    title = 'Total logs per source'
)

total_logs_per_source_fig.show()
total_logs_per_source_cost_fig

Above we can see that, the cost per log at the third source was the higher, before we observed that source 3 was also the higer marketing investment. But comparing the source 4 and source 3, we can see that:

- Source 4 had an higher amount of logs than any other marketing option;
- Source 3, had the higher investment per log, more than double of source 4.

We can conclude that, the marketing strategy using at the third source wasn't as effective as at the one used at fourth.

### ROI analysis

In [286]:
total_revenue = orders_log['Revenue'].sum()
total_cost = costs_us['costs'].sum()

In [350]:
ROI = (((total_revenue - total_cost)/total_cost)*100).round(2)
ROI

-23.42

Unfortunately, the overall result of this marketing strategy was negative. The revenue generated was insufficient to cover the marketing costs, leading the company to finish the analyzed period in deficit.